# Primitives examples

The examples in this section illustrate some common ways to use primitives. Before running these examples, follow the instructions in [Install and set up.](install-qiskit)

<Admonition type="note">
    These examples all use the primitives from Qiskit Runtime, but you could use the base primitives instead.
</Admonition>

## Estimator examples

Efficiently calculate and interpret expectation values of the quantum operators required for many algorithms with Estimator. Explore uses in molecular modeling, machine learning, and complex optimization problems.

### Run a single experiment

Use Estimator to determine the expectation value of a single circuit-observable pair.

In [2]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.quantum_info import SparsePauliOp, random_hermitian
from qiskit_ibm_runtime import QiskitRuntimeService, EstimatorV2 as Estimator

n_qubits = 50

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

mat = np.real(random_hermitian(n_qubits, seed=1234))
circuit = IQP(mat)
observable = SparsePauliOp("Z" * 50)

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(circuit)
isa_observable = observable.apply_layout(isa_circuit.layout)

estimator = Estimator(backend)
job = estimator.run([(isa_circuit, isa_observable)])
result = job.result()

print(f" > Expectation value: {result[0].data.evs}")
print(f" > Metadata: {result[0].metadata}")

 > Expectation value: 0.6071428571428571
 > Metadata: {'shots': 4096, 'target_precision': 0.015625, 'circuit_metadata': {}, 'resilience': {}, 'num_randomizations': 32}


### Run multiple experiments in a single job

Use Estimator to determine the expectation values of multiple circuit-observable pairs.

In [1]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.quantum_info import SparsePauliOp, random_hermitian
from qiskit_ibm_runtime import QiskitRuntimeService, EstimatorV2 as Estimator

n_qubits = 50

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

rng = np.random.default_rng()
mats = [np.real(random_hermitian(n_qubits, seed=rng)) for _ in range(3)]

pubs = []
circuits = [IQP(mat) for mat in mats]
observables = [
    SparsePauliOp("X" * 50),
    SparsePauliOp("Y" * 50),
    SparsePauliOp("Z" * 50),
]

# Get ISA circuits
pm = generate_preset_pass_manager(optimization_level=1, backend=backend)

for qc, obs in zip(circuits, observables):
    isa_circuit = pm.run(qc)
    isa_obs = obs.apply_layout(isa_circuit.layout)
    pubs.append((isa_circuit, isa_obs))

estimator = Estimator(backend)
job = estimator.run(pubs)
job_result = job.result()

for idx in range(len(pubs)):
    pub_result = job_result[idx]
    print(f">>> Expectation values for PUB {idx}: {pub_result.data.evs}")
    print(f">>> Standard errors for PUB {idx}: {pub_result.data.stds}")

>>> Expectation values for PUB 0: 0.1588235294117647
>>> Standard errors for PUB 0: 0.18372570722417006
>>> Expectation values for PUB 1: -0.2426470588235294
>>> Standard errors for PUB 1: 0.24287181286582873
>>> Expectation values for PUB 2: 0.01220703125
>>> Standard errors for PUB 2: 0.015620946358330926


### Run parameterized circuits

Use Estimator to run three experiments in a single job, leveraging parameter values to increase circuit reusability.

In [5]:
import numpy as np

from qiskit.circuit import QuantumCircuit, Parameter
from qiskit.quantum_info import SparsePauliOp
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import QiskitRuntimeService, EstimatorV2 as Estimator

service = QiskitRuntimeService()
backend = service.least_busy(operational=True, simulator=False)

# Step 1: Map classical inputs to a quantum problem
theta = Parameter("θ")

chsh_circuit = QuantumCircuit(2)
chsh_circuit.h(0)
chsh_circuit.cx(0, 1)
chsh_circuit.ry(theta, 0)

number_of_phases = 21
phases = np.linspace(0, 2 * np.pi, number_of_phases)
individual_phases = [[ph] for ph in phases]

ZZ = SparsePauliOp.from_list([("ZZ", 1)])
ZX = SparsePauliOp.from_list([("ZX", 1)])
XZ = SparsePauliOp.from_list([("XZ", 1)])
XX = SparsePauliOp.from_list([("XX", 1)])
ops = [ZZ, ZX, XZ, XX]

# Step 2: Optimize problem for quantum execution.

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
chsh_isa_circuit = pm.run(chsh_circuit)
isa_observables = [
    operator.apply_layout(chsh_isa_circuit.layout) for operator in ops
]

# Step 3: Execute using Qiskit primitives.

# Reshape observable array for broadcasting
reshaped_ops = np.fromiter(isa_observables, dtype=object)
reshaped_ops = reshaped_ops.reshape((4, 1))

estimator = Estimator(backend, options={"default_shots": int(1e4)})
job = estimator.run([(chsh_isa_circuit, reshaped_ops, individual_phases)])
# Get results for the first (and only) PUB
pub_result = job.result()[0]
print(f">>> Expectation values: {pub_result.data.evs}")
print(f">>> Standard errors: {pub_result.data.stds}")
print(f">>> Metadata: {pub_result.metadata}")

>>> Expectation values: [[ 1.07062932e+00  1.01475593e+00  8.60450256e-01  6.10803180e-01
   3.38093469e-01  6.89501449e-03 -3.48554870e-01 -6.15796122e-01
  -8.53079724e-01 -1.00477004e+00 -1.05826584e+00 -1.00619660e+00
  -8.46184709e-01 -6.17698195e-01 -3.19786017e-01  7.13277361e-04
   3.17883944e-01  6.12229735e-01  8.73289249e-01  1.00976298e+00
   1.06967828e+00]
 [-2.37759120e-03  3.27156550e-01  6.05572479e-01  8.58310424e-01
   1.00786091e+00  1.06397206e+00  1.00857419e+00  8.48324541e-01
   6.15796122e-01  3.00527528e-01 -4.27966417e-03 -3.38331228e-01
  -6.31963742e-01 -8.48324541e-01 -1.01118954e+00 -1.06492310e+00
  -1.01166506e+00 -8.38100899e-01 -6.20313545e-01 -3.13366521e-01
   1.16501969e-02]
 [ 3.09086856e-03 -3.46890557e-01 -6.16271640e-01 -8.30254848e-01
  -9.83371722e-01 -1.03924511e+00 -9.95021918e-01 -8.55457315e-01
  -6.17698195e-01 -3.36191396e-01  4.27966417e-03  3.38093469e-01
   6.16984917e-01  8.49751096e-01  9.97637269e-01  1.05018203e+00
   9.89791218e

### Use sessions and advanced options

Explore sessions and advanced options to optimize circuit performance on QPUs.

In [4]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.quantum_info import SparsePauliOp, random_hermitian
from qiskit_ibm_runtime import (
    QiskitRuntimeService,
    Session,
    EstimatorV2 as Estimator,
)

n_qubits = 50

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

rng = np.random.default_rng(1234)
mat = np.real(random_hermitian(n_qubits, seed=rng))
circuit = IQP(mat)
mat = np.real(random_hermitian(n_qubits, seed=rng))
another_circuit = IQP(mat)
observable = SparsePauliOp("X" * 50)
another_observable = SparsePauliOp("Y" * 50)

pm = generate_preset_pass_manager(optimization_level=1, backend=backend)
isa_circuit = pm.run(circuit)
another_isa_circuit = pm.run(another_circuit)
isa_observable = observable.apply_layout(isa_circuit.layout)
another_isa_observable = another_observable.apply_layout(
    another_isa_circuit.layout
)

with Session(backend=backend) as session:
    estimator = Estimator(mode=session)

    estimator.options.resilience_level = 1

    job = estimator.run([(isa_circuit, isa_observable)])
    another_job = estimator.run(
        [(another_isa_circuit, another_isa_observable)]
    )
    result = job.result()
    another_result = another_job.result()

    # first job
    print(f" > Expectation value: {result[0].data.evs}")
    print(f" > Metadata: {result[0].metadata}")

    # second job
    print(f" > Another Expectation value: {another_result[0].data.evs}")
    print(f" > More Metadata: {another_result[0].metadata}")

 > Expectation value: 0.01123046875
 > Metadata: {'shots': 4096, 'target_precision': 0.015625, 'circuit_metadata': {}, 'resilience': {}, 'num_randomizations': 32}
 > Another Expectation value: -0.34210526315789475
 > More Metadata: {'shots': 4096, 'target_precision': 0.015625, 'circuit_metadata': {}, 'resilience': {}, 'num_randomizations': 32}


<span id="sampler-examples"></span>
## Sampler examples

Generate entire error-mitigated quasi-probability distributions sampled from quantum circuit outputs. Leverage Sampler’s capabilities for search and classification algorithms like Grover’s and QVSM.

### Run a single experiment

Use Sampler to return the measurement outcome as bitstrings or counts of a single circuit.

In [10]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.quantum_info import random_hermitian
from qiskit_ibm_runtime import QiskitRuntimeService, SamplerV2 as Sampler

n_qubits = 127

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

mat = np.real(random_hermitian(n_qubits, seed=1234))
circuit = IQP(mat)
circuit.measure_all()

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(circuit)

sampler = Sampler(backend)
job = sampler.run([isa_circuit])
result = job.result()

# Get results for the first (and only) PUB
pub_result = result[0]

print(f" > Counts: {pub_result.data.meas.get_counts()}")

 > Counts: {'0011001100111110001110000000100011001101101001010011110011001010001000010000100010110010110101000000101111001000001100100000100': 1, '1011001001010110101100011100100101110100000110000001000101000100010001000100100000110000000100000000001100001010001000100101001': 1, '0101111000110100101001000101010111010001000001000000100010000000001000001000010100000010100100000000101000011000101001100110100': 1, '1011000001111111111000000100101001001010100000000010101000101000001000000100011000100010000001001110010110000010001000101000101': 1, '0101111010110100000100001101010001010001110010000000101111001000100010101101000110100000111101001010100000010010001000110110111': 1, '1010101000011010001111010100000001010011000100001111001001110100000110010000000100110000011000000110011000001000001000010000101': 1, '1110000001010110111000000000101011011111101010011000110011100110111001010100000000010000101001000000010110001000001010000000000': 1, '1001100000000100010011100110010011000001001100010

### Run multiple experiments in a single job

Use Sampler to return the measurement outcome as bitstrings or counts of multiple circuits in one job.

In [11]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.quantum_info import random_hermitian
from qiskit_ibm_runtime import QiskitRuntimeService, SamplerV2 as Sampler

n_qubits = 127

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

rng = np.random.default_rng()
mats = [np.real(random_hermitian(n_qubits, seed=rng)) for _ in range(3)]
circuits = [IQP(mat) for mat in mats]
for circuit in circuits:
    circuit.measure_all()

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuits = pm.run(circuits)

sampler = Sampler(backend)
job = sampler.run(isa_circuits)
result = job.result()

for idx, pub_result in enumerate(result):
    print(f" > Counts for pub {idx}: {pub_result.data.meas.get_counts()}")

 > Counts for pub 0: {'0001000100111011000101000001001100100001100000100100000001000001000000001000000000010000001001100010100000100000000000001001100': 1, '1000100110001111110101000111011100001001010000100100000000001011000000000011000011011010010010000100100100101100001100000001000': 1, '1101010010111101100001100101010000100101000101011010001100101100001001000100000110011000011000110001101100001010000000010001000': 1, '0011010010010100001010100000000000000100100100000010000110001110100000101000000110010011000011110011101000101000101100001000001': 1, '1100010011010111011000101100101000000101000000100000010000001001000000000101000100001000010000100001001001000000100100000000100': 1, '1111101110110100111000001100101100010000000100101010000000000000101001001101000000011011010000100000000000001010000100001001001': 1, '1010100101101010010111000101110100000001000000110110010000100010001000101010000101001001001010110011101001001000000100000101101': 1, '110101111100110100110110100100000100001

### Run parameterized circuits

Run several experiments in a single job, leveraging parameter values to increase circuit reusability.

In [12]:
import numpy as np
from qiskit.circuit.library import RealAmplitudes
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import QiskitRuntimeService, SamplerV2 as Sampler

n_qubits = 127

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

# Step 1: Map classical inputs to a quantum problem
circuit = RealAmplitudes(num_qubits=n_qubits, reps=2)
circuit.measure_all()

# Define three sets of parameters for the circuit
rng = np.random.default_rng(1234)
parameter_values = [
    rng.uniform(-np.pi, np.pi, size=circuit.num_parameters) for _ in range(3)
]

# Step 2: Optimize problem for quantum execution.

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(circuit)

# Step 3: Execute using Qiskit primitives.
sampler = Sampler(backend)
job = sampler.run([(isa_circuit, parameter_values)])
result = job.result()
# Get results for the first (and only) PUB
pub_result = result[0]
# Get counts from the classical register "meas".
print(
    f" >> Counts for the meas output register: {pub_result.data.meas.get_counts()}"
)

 >> Counts for the meas output register: {'0001000101100001100001100000010001001100100001110001010000100101110001000000100000001011011101011100000100000110011001000010100': 1, '1011000011010000100011111000111011110000001001110001001000010011100101111000111000000011110111011011010000010001100001110011000': 1, '1111000110000001110000010000111011111000000101010010010001101001001101110000001000010000100101111101110010101010011001110001010': 1, '1011100111000001110010111100001011011000100011010000010010001001100101100000000100010001001101100100000000000101101110010000101': 1, '1011100111010001110111110000110010110100010011000011010011101101000111010001001000011010010111010100010110110101101100000010111': 1, '0111100001000101100000011000110011101000101011010011010110100100110001000000011010110010010111000001010101010100010100110001101': 1, '1110110000111101110000111000110011111100100110000111010011000001011101001111111110000011111111010000010011101111011010010010100': 1, '1111110110010001110

### Use sessions and advanced options

Explore sessions and advanced options to optimize circuit performance on QPUs.

In [13]:
import numpy as np
from qiskit.circuit.library import IQP
from qiskit.quantum_info import random_hermitian
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import Session, SamplerV2 as Sampler
from qiskit_ibm_runtime import QiskitRuntimeService

n_qubits = 127

service = QiskitRuntimeService()
backend = service.least_busy(
    operational=True, simulator=False, min_num_qubits=n_qubits
)

rng = np.random.default_rng(1234)
mat = np.real(random_hermitian(n_qubits, seed=rng))
circuit = IQP(mat)
circuit.measure_all()
mat = np.real(random_hermitian(n_qubits, seed=rng))
another_circuit = IQP(mat)
another_circuit.measure_all()

pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(circuit)
another_isa_circuit = pm.run(another_circuit)

with Session(backend=backend) as session:
    sampler = Sampler(mode=session)
    job = sampler.run([isa_circuit])
    another_job = sampler.run([another_isa_circuit])
    result = job.result()
    another_result = another_job.result()

# first job
print(f" > Counts for job 1: {result[0].data.meas.get_counts()}")

 > Counts for job 1: {'1101010000011001100000011110010011000101111000000000000000000000010011000001000110000000101000100001000010011010010000000000000': 1, '0110001101000100000010011110010000100100000110010010000000000000010110000000000010010010010001000110000100011011000100110010100': 1, '0001010110000101111110000110000000000110010101100100000100000000010111000001000000011000111011100110100010000001010101110000000': 1, '1100000001001110000101101101000111000001001000000000011000000000000110000000110011010010001000101111100110000010010100000011000': 1, '0011100100000000100011100011010001000001001010110100000000000000000101000000000000000010010010100010100100001001001001010010001': 1, '0100010011000101100000000000110100001001001001110101000100000000110001010001000000010000100000100101000100001000010001010010100': 1, '1001001010110000100011001110011111000010000111010000010000000000100111000101000100010010110011010001000010001010000001110000000': 1, '101111010001101000010000010000100001101

In [14]:
# second job
print(f" > Counts for job 2: {another_result[0].data.meas.get_counts()}")

 > Counts for job 2: {'0111000011101010101000101001000010101001000000000111101000010000001000011010000100000010010100111000100000001000000100101000001': 1, '1110100011000010100100001001010010000100001010100010001001010010000110100110110000000110001010111000101000001010001000000000000': 1, '1100000000010110010001000111000111101011010000000110100001000010001010111000100100010110010100011100101000000110000000110000011': 1, '0111101110100001000100001001000010111000100001000101100001000010000001100100010000110110001010100010101000000110000101100000001': 1, '0010100100000100100100010011000010001001000010000000000001000000000000110110100000000111011010000100100000001110110001000100000': 1, '0011001110100110100000100000000110000101001011000111100000010010000010001000000010000110001000000000100000010110100100100000001': 1, '1101110100110100000101110110010110001011000011000110101000010000010010011101001000000010001011101001101000001100000000000000001': 1, '101100101011010010110001011001100000000

## Next steps

<Admonition type="tip" title="Recommendations">
    - [Specify advanced runtime options.](runtime-options-overview)
    - Practice with primitives by working through the [Cost function lesson](https://learning.quantum.ibm.com/course/variational-algorithm-design/cost-functions#primitives) in IBM Quantum Learning.
    - Learn how to transpile locally in the [Transpile](./transpile/) section.
    - Try the [Submit pre-transpiled circuits](https://learning.quantum.ibm.com/tutorial/submitting-user-transpiled-circuits-using-primitives) tutorial.
    - Read [Migrate to V2 primitives](/migration-guides/v2-primitives).
    - Understand the [Job limits](/guides/job-limits) when sending a job to an IBM&reg; QPU.
</Admonition>